# Document Clusters

In [1]:
%load_ext autoreload
%autoreload 2
from cord import ResearchPapers

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\dwight\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [2]:
research_papers = ResearchPapers.from_pickle()

In [3]:
since_covid = research_papers.after('2019-08-30')
since_covid.nlp()

Getting gensim LDA topic model
Assigning LDA topics


In [5]:
import pandas as pd
import numpy as np
from gensim.matutils import hellinger, kullback_leibler, jaccard
import altair as alt

metadata = since_covid.metadata.copy()
metadata = metadata[ ~(metadata.abstract == "")]

# if the published date is greater than today assign it a random date in the past 4 months
enddate = '2020-03-24'
after_enddate = metadata.published > enddate

enddate_pd = pd.to_datetime(enddate)
def assign_random_date(date):
    return enddate_pd + pd.DateOffset(days=-np.random.randint(1, 110))

metadata.loc[after_enddate, 'published'] = \
    metadata.loc[after_enddate, 'published'].apply(assign_random_date)

In [6]:

def distance_from_mean_document(topic_vectors):
    mean_vector = np.mean(topic_vectors)
    return topic_vectors.apply(lambda v: hellinger(v, mean_vector))

def plot_distribution(metadata):
    df = metadata.loc[~(metadata.abstract =='') & ~(metadata.published ==''),
                      ['topic_vector', 'published', 'top_topic', 'abstract']]
    df['topic_distance'] = distance_from_mean_document(df.topic_vector)
    chart = alt.Chart(df).mark_circle().encode(
        x = 'published:T',
        y = 'topic_distance:Q',
        color = 'top_topic:N'
    )
    return df, chart
    
df, chart = plot_distribution(metadata)
chart

alt.Chart(...)